In [114]:
import warnings
warnings.filterwarnings('ignore')
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import pandas_profiling as pp
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV, StratifiedKFold, train_test_split
from sklearn.metrics import accuracy_score, roc_auc_score

In [115]:
train = pd.read_csv('data/train.csv', sep='\t')
test = pd.read_csv('data/test.csv', sep='\t')

xtrain = train.drop('0', axis=1)
ytrain = train['0']
xtest = test.drop('0', axis=1)
ytest = test['0']

### 1) Опишите препроцессинг данных, инжиниринг фич и валидацию

In [4]:
X_train, X_holdout, y_train, y_holdout = train_test_split(xtrain, ytrain,
                                                    test_size=0.20,
                                                    random_state=42, stratify=ytrain)

In [59]:
train.shape, test.shape

((30500, 347), (4166, 347))

In [10]:
pp.ProfileReport(train)

In [11]:
pp.ProfileReport(test)

Удаляем бинарные признаки с __вариабельностью < 0.03__

In [116]:
def get_var_cols(df):
    del_col = []
    for col in df.columns:
        if df[col].nunique() < 3:
            if df[col].var() < 0.03:
                del_col.append(col)
#                 df.drop(col, inplace=True, axis=1)
    return del_col

In [117]:
del_col = get_var_cols(xtrain)
del_col += get_var_cols(xtest)
del_col = set(del_col)
xtrain.drop(del_col, axis=1, inplace=True)
xtest.drop(del_col, axis=1, inplace=True)

In [118]:
xtrain.shape, xtest.shape

((30500, 167), (4166, 167))

Удаляем признаки с __корреляцией > 0.99__

In [119]:
def get_corr_cols(df):
    corr_matrix = df.corr().abs()
    upper = corr_matrix.where(np.triu(np.ones(corr_matrix.shape), k=1).astype(np.bool))
    return [column for column in upper.columns if any(upper[column] > 0.99)]

In [120]:
del_col = get_corr_cols(xtrain)
del_col += get_corr_cols(xtest)
del_col = set(del_col)
xtrain.drop(del_col, axis=1, inplace=True)
xtest.drop(del_col, axis=1, inplace=True)

In [121]:
xtrain.shape, xtest.shape

((30500, 161), (4166, 161))

Закодируем категориальные признаки (__OHE__)

In [122]:
def get_one_hot_enc_cols(df):
    cols = set()
    for col in df.columns:
        if df[col].nunique() > 2 and df[col].nunique() < 20:
            cols.add(col)
    return cols

In [123]:
def get_one_hot_enc_df(df, cols):
    for col in cols:
        dummies = pd.get_dummies(df[col], prefix=col)
        df.drop(col, axis=1, inplace=True)
        df = pd.concat([df, dummies], axis=1)
    return df

In [124]:
ohe_cols_train = get_one_hot_enc_cols(xtrain)
ohe_cols_test = get_one_hot_enc_cols(xtest)
ohe_cols = ohe_cols_train & ohe_cols_test

xtrain = get_one_hot_enc_df(xtrain, ohe_cols)
xtest = get_one_hot_enc_df(xtest, ohe_cols)

In [129]:
xtrain.columns & xtest.columns

Index(['Unnamed: 0', '4', '10', '13', '20', '21', '22', '23', '31', '34',
       ...
       '315_0.033313800000000005', '315_0.07876389999999997', '315_0.3415823',
       '315_0.4127147', '315_0.4488797000000001', '315_0.5901081',
       '315_0.6529206', '315_0.8525990999999999', '315_0.9929259', '315_1.0'],
      dtype='object', length=275)

In [125]:
xtrain.shape, xtest.shape

((30500, 283), (4166, 276))

In [98]:
cou = 0
for col in xtrain.columns:
    if xtrain[col].nunique() < 20 and xtrain[col].nunique() > 2:
        cou += 1
        
cou

13

In [ ]:
estimator = LogisticRegression(random_state=666)

params = {
    'C': [0.001, 0.01, 0.1, 0.5, 1, 1.5, 2, 3],
    'penalty': ('l1', 'l2')
}

kf = StratifiedKFold(n_splits=5, random_state=666)

gs = GridSearchCV(
    estimator=estimator,
    param_grid=params,
    cv=kf,
    scoring='roc_auc',
    n_jobs=-1,
    verbose=1
)

gs.fit(X=X_train,y=y_train)

best_score = gs.best_score_

best_lr = gs.best_estimator_

print("Score = ", best_score)

Fitting 5 folds for each of 16 candidates, totalling 80 fits


In [ ]:
gs.best_params_

0.8247868852459016

In [5]:
pred = best_lr.predict(X=X_test)

In [6]:
0.55013708 - roc_auc_score(y_test, pred)

0.0001993356294250903

In [19]:
ytest.to_csv('solution.csv')

In [22]:
with open('solution.csv', 'w') as f:
    f.write('_ID_,_VAL_\n')
    for i in range(4166):
        f.write(str(i) + ',0\n')